https://www.kdnuggets.com/deploying-your-first-machine-learning-model

In [4]:
try:
    import opendatasets as od
    import pandas as pd
except:
    !pip install opendatasets
    import opendatasets as od
from os import path

url = "https://www.kaggle.com/datasets/uciml/glass"  ### kaggle dataset url here
data_dir = "/content/"  ### directory where you want to save data

# Go to the account tab and under API section, click Create New API Token.

# A JSON file will be downloaded, open it locally or you can also use any online JSON viewer and upload it there.

# On opening this file, you will find the username and key in it. Copy the username and password and paste it into the prompted Notebook cell.
# The content of the downloaded file would look like this.

#               {"username":<KAGGLE USERNAME>,"key":<KAGGLE KEY>}


def download_data(url, data_dir):
    od.download(url, data_dir)

In [2]:
#  comment out below if you already have the data downloaded
# download_data(url, data_dir)

In [5]:
import pandas as pd
#  use path below for colab
# glass_df = pd.read_csv("/content/glass/glass.csv")
glass_df = pd.read_csv("glass.csv")

glass_df = glass_df.sample(frac = 1)
glass_df.head(3)

RI     Na    Mg    Al     Si     K     Ca   Ba    Fe  Type
55   1.51769  12.45  2.71  1.29  73.70  0.56   9.06  0.0  0.24     1
184  1.51115  17.38  0.00  0.34  75.41  0.00   6.65  0.0  0.00     6
103  1.52725  13.80  3.15  0.66  70.57  0.08  11.64  0.0  0.00     2

In [6]:
from sklearn.model_selection import train_test_split

X = glass_df.drop("Type",axis=1)
y = glass_df.Type

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=125)

In [7]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline


pipe = Pipeline(
    steps=[
        ("imputer", SimpleImputer()),
        ("scaler", StandardScaler()),
        ("model", RandomForestClassifier(n_estimators=100, random_state=125)),
    ]
)
pipe.fit(X_train, y_train)

pipe.score(X_test, y_test)

0.7846153846153846

In [8]:
from sklearn.metrics import classification_report

y_pred = pipe.predict(X_test)
print(classification_report(y_test,y_pred))

              precision    recall  f1-score   support

           1       0.70      0.91      0.79        23
           2       0.87      0.80      0.83        25
           3       1.00      0.33      0.50         6
           5       0.67      1.00      0.80         2
           6       1.00      1.00      1.00         2
           7       0.80      0.57      0.67         7

    accuracy                           0.78        65
   macro avg       0.84      0.77      0.77        65
weighted avg       0.81      0.78      0.77        65



In [8]:
!pip install skops

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 120.7/120.7 kB 1.4 MB/s eta 0:00:00


In [9]:
import skops.io as sio
sio.dump(pipe, "glass_pipeline.skops")

In [10]:
sio.load("glass_pipeline.skops", trusted=True)


Pipeline(steps=[('imputer', SimpleImputer()), ('scaler', StandardScaler()),
                ('model', RandomForestClassifier(random_state=125))])

In [11]:
!pip install gradio

In [12]:
!pip install --upgrade typing



In [1]:
import gradio as gr
import skops.io as sio

pipe = sio.load("glass_pipeline.skops", trusted=True)

classes = [
    "None",
    "Building Windows Float Processed",
    "Building Windows Non Float Processed",
    "Vehicle Windows Float Processed",
    "Vehicle Windows Non Float Processed",
    "Containers",
    "Tableware",
    "Headlamps",
]


def classifier(RI, Na, Mg, Al, Si, K, Ca, Ba, Fe):
    pred_glass = pipe.predict([[RI, Na, Mg, Al, Si, K, Ca, Ba, Fe]])[0]
    label = f"Predicted Glass label: **{classes[pred_glass]}**"
    return label


inputs = [
    gr.Slider(1.51, 1.54, step=0.01, label="Refractive Index"),
    gr.Slider(10, 17, step=1, label="Sodium"),
    gr.Slider(0, 4.5, step=0.5, label="Magnesium"),
    gr.Slider(0.3, 3.5, step=0.1, label="Aluminum"),
    gr.Slider(69.8, 75.4, step=0.1, label="Silicon"),
    gr.Slider(0, 6.2, step=0.1, label="Potassium"),
    gr.Slider(5.4, 16.19, step=0.1, label="Calcium"),
    gr.Slider(0, 3, step=0.1, label="Barium"),
    gr.Slider(0, 0.5, step=0.1, label="Iron"),
]
outputs = [gr.Label(num_top_classes=7)]

title = "Glass Classification"
description = "Enter the details to correctly identify glass type?"

gr.Interface(
    fn=classifier,
    inputs=inputs,
    outputs=outputs,
    title=title,
    description=description,
).launch()

Exception in thread Thread-5 (attachment_entry):
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/debugpy/server/api.py", line 237, in listen
    sock, _ = endpoints_listener.accept()
  File "/usr/lib/python3.10/socket.py", line 293, in accept
    fd, addr = self._accept()
TimeoutError: timed out

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/local/lib/python3.10/dist-packages/google/colab/_debugpy.py", line 52, in attachment_entry
    debugpy.listen(_dap_port)
  File "/usr/local/lib/python3.10/dist-packages/debugpy/public_api.py", line 31, in wrapper
    return wrapped(*args, **kwargs)
  File "/usr/local/lib/python3.10/dist-packages/debugpy/server/api.py", line 143, in debug
    log.reraise

Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
Running on public URL: https://efa6ecf31e4b5a440c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
